# This Notebook will be mainly used for the capstone project

In [196]:
import pandas as pd
import numpy as np

In [197]:
print("Hello Capstone Project Course!")

Hello Capstone Project Course!


## 1. Import of necessary packages and libraries

In [198]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
#import folium # map rendering library

print('Libraries imported.')

Libraries imported.


## 2. Import of necessary data and preparation of data

In [199]:
# Read all districts from "https://offenedaten.frankfurt.de/dataset/strassenverzeichnis-der-stadt-frankfurt-am-main"

url = "https://offenedaten.frankfurt.de/dataset/7bd9de80-98de-45c2-99a8-497ce7b3c82c/resource/d937da11-da40-4614-95f3-6917469709ff/download/zprojekteopen-datadatenamt-12strassenverzeichnis2019strassenverzeichnis2019.xlsx"
df = pd.read_excel(url)

In [200]:
ffm_data = df[['Stadtbezirk', 'Stadtteil Name', 'Postleitzahl']]

In [201]:
ffm_data = ffm_data.groupby('Stadtteil Name').count()

In [202]:
#Create List with the names of all districts in Frankfurt am Main

districts = []
for i in range(len(ffm_data)):
    districts.append(ffm_data.iloc[i].name)

In [203]:
url2 = "https://offenedaten.frankfurt.de/dataset/3be1af84-12d5-4d91-979a-3a468c77ed4e/resource/57bc2f7c-60ed-4511-83b3-dbc6542f38de/download/bevoelkerung.xls"
df2 = pd.read_excel(url2)
ffm_pop = df2.iloc[:,1:3]
ffm_pop.rename(columns={ ffm_pop.columns[0]: "District", ffm_pop.columns[1]: "Population" }, inplace = True)
ffm_pop = ffm_pop[:-1]

In [204]:
ffm_pop['District'] = ffm_pop['District'].replace(['Bahnhofsviertel'], 'Gutleut-/Bahnhofsviertel')

In [205]:
new = 3117 + 5952
ffm_pop['Population'] = ffm_pop['Population'].replace([3117], new)

In [206]:
#ffm_pop = ffm_pop.drop(9)
ffm_pop.reset_index(drop=True)

District  Population
0                   Altstadt        3601
1                 Innenstadt        6334
2   Gutleut-/Bahnhofsviertel        9069
3                Westend-Süd       17076
4               Westend-Nord        9083
5               Nordend-West       28262
6                Nordend-Ost       25410
7                     Ostend       26540
8                   Bornheim       26105
9             Gutleutviertel        5952
10                    Gallus       28165
11                Bockenheim       35789
12        Sachsenhausen-Nord       29789
13         Sachsenhausen-Süd       25786
14                   Oberrad       12561
15                 Niederrad       22396
16                Schwanheim       20480
17                 Griesheim       23124
18                 Rödelheim       17026
19                    Hausen        7172
20                 Praunheim       15700
21               Heddernheim       16747
22               Niederursel       15081
23                  Ginnheim       16346
24                 Dornbusch       17817
25               Eschersheim       14381
26                 Eckenheim       14062
27              Preungesheim       13934
28                   Bonames        6139
29               Berkersheim        3643
30                Riederwald        4664
31                  Seckbach        9938
32                Fechenheim       15913
33                    Höchst       14143
34                      Nied       18294
35                Sindlingen        8881
36                 Zeilsheim       11927
37           Unterliederbach       14609
38                Sossenheim       15252
39          Nieder-Erlenbach        4588
40          Kalbach-Riedberg       12019
41                   Harheim        4304
42           Nieder-Eschbach       11351
43            Bergen-Enkheim       17563
44          Frankfurter Berg        7627

In [207]:
#get geojson from frankfurt districts
!wget -q -O 'frankfurt_data.json' https://offenedaten.frankfurt.de/dataset/85b38876-729c-4a78-910c-a52d5c6df8d2/resource/84dff094-ab75-431f-8c64-39606672f1da/download/ffmstadtteilewahlen.geojson

In [208]:
with open('frankfurt_data.json') as json_data:
    frankfurt_data = json.load(json_data)

In [209]:
!pip -q install folium

In [210]:
import folium

map_ffm = folium.Map(location=[50.110924, 8.682127], zoom_start=14)

In [211]:
map_ffm.choropleth(geo_data=frankfurt_data,
    data=ffm_pop,
    columns=['District', 'Population'],
    key_on='feature.properties.STTLNAME',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Population Density Frankfurt'
)


/opt/conda/envs/Python-3.7-main/lib/python3.7/site-packages/folium/folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


In [212]:
folium.GeoJson(open('frankfurt_data.json', 'r', encoding='utf-8-sig').read(),
               name = 'District',
               tooltip=folium.GeoJsonTooltip(fields=('STTLNAME',),
               aliases=('District',)),
               show = True).add_to(map_ffm)

In [213]:
map_ffm

In [214]:
# Name of Data Frames:
# Population Data: ffm_pop
# GeoData: frankfurt_data (original) location_data (with single longitude/latitude value)
# List of Districts: districts

districts[1] = 'Gutleut-/Bahnhofsviertel'
districts.pop(16)

'Gutleutviertel'

In [215]:
address = "Sachsenhausen-Süd"

geolocator = Nominatim(user_agent="ffm_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

print('The geograpical coordinate of Eschersheim are {}, {}.'.format(latitude, longitude))


The geograpical coordinate of Eschersheim are 50.0707248, 8.685449728161462.


In [216]:
loc_data = ffm_pop[::]

In [217]:
column_names = ['District','Latitude', 'Longitude']
location_data = pd.DataFrame(columns=column_names)

In [218]:
for item in loc_data['District']:
    geolocator = Nominatim(user_agent="ffm_explorer")
    location = geolocator.geocode(item+" Frankfurt")
    latitude = location.latitude
    longitude = location.longitude
    
    location_data = location_data.append({'District': item, 'Latitude': latitude, 'Longitude': longitude}, ignore_index=True)

In [219]:
# Foursquare credentials
CLIENT_ID = 'CAYSYJQ3O0EXR3HOPBKV4XRMXHY4PYBFP0U1YVR3PWS50OG5' # your Foursquare ID
CLIENT_SECRET = 'YAOLZQCONKCO21NEQTVX1ADRNZNP5KTUCHJAJLCHATULNL4R' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: CAYSYJQ3O0EXR3HOPBKV4XRMXHY4PYBFP0U1YVR3PWS50OG5
CLIENT_SECRET:YAOLZQCONKCO21NEQTVX1ADRNZNP5KTUCHJAJLCHATULNL4R


In [220]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['District', 
                  'District Latitude', 
                  'District Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [221]:
frankfurt_venues = getNearbyVenues(names=location_data['District'], latitudes=location_data['Latitude'], longitudes=location_data['Longitude'])

Altstadt
Innenstadt
Gutleut-/Bahnhofsviertel
Westend-Süd
Westend-Nord
Nordend-West
Nordend-Ost
Ostend
Bornheim
Gutleutviertel
Gallus
Bockenheim
Sachsenhausen-Nord
Sachsenhausen-Süd
Oberrad
Niederrad
Schwanheim
Griesheim
Rödelheim
Hausen
Praunheim
Heddernheim
Niederursel
Ginnheim
Dornbusch
Eschersheim
Eckenheim
Preungesheim
Bonames
Berkersheim
Riederwald
Seckbach
Fechenheim
Höchst
Nied
Sindlingen
Zeilsheim
Unterliederbach
Sossenheim
Nieder-Erlenbach
Kalbach-Riedberg
Harheim
Nieder-Eschbach
Bergen-Enkheim
Frankfurter Berg


In [29]:
frankfurt_venues

District  District Latitude  District Longitude  \
0                    Altstadt          50.110442            8.682901   
1                    Altstadt          50.110442            8.682901   
2                    Altstadt          50.110442            8.682901   
3                    Altstadt          50.110442            8.682901   
4                    Altstadt          50.110442            8.682901   
5                    Altstadt          50.110442            8.682901   
6                    Altstadt          50.110442            8.682901   
7                    Altstadt          50.110442            8.682901   
8                    Altstadt          50.110442            8.682901   
9                    Altstadt          50.110442            8.682901   
10                   Altstadt          50.110442            8.682901   
11                   Altstadt          50.110442            8.682901   
12                   Altstadt          50.110442            8.682901   
13                   Altstadt          50.110442            8.682901   
14                   Altstadt          50.110442            8.682901   
15                   Altstadt          50.110442            8.682901   
16                   Altstadt          50.110442            8.682901   
17                   Altstadt          50.110442            8.682901   
18                   Altstadt          50.110442            8.682901   
19                   Altstadt          50.110442            8.682901   
20                   Altstadt          50.110442            8.682901   
21                   Altstadt          50.110442            8.682901   
22                   Altstadt          50.110442            8.682901   
23                   Altstadt          50.110442            8.682901   
24                   Altstadt          50.110442            8.682901   
25                   Altstadt          50.110442            8.682901   
26                   Altstadt          50.110442            8.682901   
27                   Altstadt          50.110442            8.682901   
28                   Altstadt          50.110442            8.682901   
29                   Altstadt          50.110442            8.682901   
30                   Altstadt          50.110442            8.682901   
31                   Altstadt          50.110442            8.682901   
32                   Altstadt          50.110442            8.682901   
33                   Altstadt          50.110442            8.682901   
34                   Altstadt          50.110442            8.682901   
35                   Altstadt          50.110442            8.682901   
36                   Altstadt          50.110442            8.682901   
37                   Altstadt          50.110442            8.682901   
38                   Altstadt          50.110442            8.682901   
39                   Altstadt          50.110442            8.682901   
40                   Altstadt          50.110442            8.682901   
41                   Altstadt          50.110442            8.682901   
42                   Altstadt          50.110442            8.682901   
43                   Altstadt          50.110442            8.682901   
44                   Altstadt          50.110442            8.682901   
45                   Altstadt          50.110442            8.682901   
46                   Altstadt          50.110442            8.682901   
47                   Altstadt          50.110442            8.682901   
48                   Altstadt          50.110442            8.682901   
49                   Altstadt          50.110442            8.682901   
50                   Altstadt          50.110442            8.682901   
51                   Altstadt          50.110442            8.682901   
52                   Altstadt          50.110442            8.682901   
53                   Altstadt          50.110442            8.682901   
54                   Altstadt          50.110442            8

In [140]:
df2.head()

Codes        Stadtteil  Bevölkerung Einwohnerinnen und Einwohner  2012  \
0     1         Altstadt                                            3601   
1     2       Innenstadt                                            6334   
2     3  Bahnhofsviertel                                            3117   
3     4      Westend-Süd                                           17076   
4     5     Westend-Nord                                            9083   

   Bevölkerung Einwohnerinnen und Einwohner  diff  \
0                                             NaN   
1                                             NaN   
2                                             NaN   
3                                             NaN   
4                                             NaN   

   Bevölkerung Einwohnerinnen und Einwohner  target  \
0                                               NaN   
1                                               NaN   
2                                               NaN   
3                                               NaN   
4                                               NaN   

   Bevölkerung Durchschnittsalter  2012  Bevölkerung Durchschnittsalter  diff  \
0                                  43.4                                   2.1   
1                                  41.6                                   0.3   
2                                  37.5                                  -3.8   
3                                  40.7                                  -0.6   
4                                  40.0                                  -1.3   

   Bevölkerung Durchschnittsalter  target  \
0                                     NaN   
1                                     NaN   
2                                     NaN   
3                                     NaN   
4                                     NaN   

   Bevölkerung Einwohnerinnen und Einwohner unter 18 Jahren in %  2012  \
0                                               10.1                     
1                                                9.0                     
2                                                7.7                     
3                                               14.4                     
4                                               15.9                     

   Bevölkerung Einwohnerinnen und Einwohner unter 18 Jahren in %  diff  \
0                                               -5.8                     
1                                               -6.9                     
2                                               -8.2                     
3                                               -1.5                     
4                                                0.0                     

   Bevölkerung Einwohnerinnen und Einwohner unter 18 Jahren in %  target  \
0                                                NaN                       
1                                                NaN                       
2                                                NaN                       
3                                                NaN                       
4                                                NaN                       

   Bevölkerung Einwohnerinnen und Einwohner von 18 bis 64 Jahren in %  2012  \
0                                               73.0                          
1                                               76.5                          
2                                               85.6                          
3                                               70.5                          
4                                               69.0                          

   Bevölkerung Einwohnerinnen und Einwohner von 18 bis 64 Jahren in %  diff  \
0                                                5.2                          
1                                                8.7                          
2                                               17.8                          

In [222]:
df_wm = df2.iloc[:, 1:3]
df_wm['Target'] = df2.iloc[:,11]

In [223]:
df_wm = df_wm.rename(columns={"Bevölkerung Einwohnerinnen und Einwohner  2012": "Population"})
df_wm = df_wm.rename(columns={"Stadtteil": "District"})

In [224]:
df_wm['Target'] = df_wm['Target'].apply(lambda x:x/100)
df_wm.head()

District  Population  Target
0         Altstadt        3601   0.730
1       Innenstadt        6334   0.765
2  Bahnhofsviertel        3117   0.856
3      Westend-Süd       17076   0.705
4     Westend-Nord        9083   0.690

In [225]:
df_wm['Target'] = df_wm['Target']*df_wm['Population']
df_wm.head()

District  Population     Target
0         Altstadt        3601   2628.730
1       Innenstadt        6334   4845.510
2  Bahnhofsviertel        3117   2668.152
3      Westend-Süd       17076  12038.580
4     Westend-Nord        9083   6267.270

In [278]:
df_wmf = df_wm[::]

In [279]:
df_wmf[['Target']] = df_wmf[['Target']].astype(int)

In [280]:
df_wmf['District'] = df_wmf['District'].replace(['Bahnhofsviertel'], 'Gutleut-/Bahnhofsviertel')
#ffm_pop['District'] = ffm_pop['District'].replace(['Bahnhofsviertel'], 'Gutleut-/Bahnhofsviertel')

In [281]:
new2 = 2668 + 4404
df_wmf['Target'] = df_wmf['Target'].replace([2668], new2)

In [284]:
#df_wmf.drop(9)
df_wmf.reset_index(drop=True)

District  Population  Target
0                   Altstadt        3601    2628
1                 Innenstadt        6334    4845
2   Gutleut-/Bahnhofsviertel        3117    7072
3                Westend-Süd       17076   12038
4               Westend-Nord        9083    6267
5               Nordend-West       28262   20489
6                Nordend-Ost       25410   19108
7                     Ostend       26540   19082
8                   Bornheim       26105   18012
9             Gutleutviertel        5952    4404
10                    Gallus       28165   20757
11                Bockenheim       35789   26841
12        Sachsenhausen-Nord       29789   21299
13         Sachsenhausen-Süd       25786   16709
14                   Oberrad       12561    8378
15                 Niederrad       22396   15610
16                Schwanheim       20480   12492
17                 Griesheim       23124   16209
18                 Rödelheim       17026   11458
19                    Hausen        7172    4733
20                 Praunheim       15700    9749
21               Heddernheim       16747   10634
22               Niederursel       15081    9139
23                  Ginnheim       16346   10445
24                 Dornbusch       17817   11313
25               Eschersheim       14381    9419
26                 Eckenheim       14062    9266
27              Preungesheim       13934    9029
28                   Bonames        6139    3892
29               Berkersheim        3643    2214
30                Riederwald        4664    3064
31                  Seckbach        9938    6211
32                Fechenheim       15913   10311
33                    Höchst       14143    9999
34                      Nied       18294   12055
35                Sindlingen        8881    5692
36                 Zeilsheim       11927    7323
37           Unterliederbach       14609    9452
38                Sossenheim       15252    9791
39          Nieder-Erlenbach        4588    2876
40          Kalbach-Riedberg       12019    8016
41                   Harheim        4304    2698
42           Nieder-Eschbach       11351    7196
43            Bergen-Enkheim       17563   11170
44          Frankfurter Berg        7627    5026
45         Frankfurt am Main      678691  460152

### Data preparation is finished

## 3. Analysis of Data

In [30]:
# Analyze the districts

#one hot encoding
frankfurt_onehot = pd.get_dummies(frankfurt_venues[['Venue Category']], prefix="", prefix_sep="")

# add district column to the df
frankfurt_onehot['District'] = frankfurt_venues['District']

#move district to first column
fixed_columns = [frankfurt_onehot.columns[-1]] + list(frankfurt_onehot.columns[:-1])
frankfurt_onehot = frankfurt_onehot[fixed_columns]

In [34]:
#create groups by district and count mean of freq occur
frankfurt_grouped = frankfurt_onehot.groupby('District').mean().reset_index()
frankfurt_grouped.head()

District  African Restaurant  American Restaurant  Apple Wine Pub  \
0        Altstadt                 0.0                  0.0             0.0   
1  Bergen-Enkheim                 0.0                  0.0             0.0   
2     Berkersheim                 0.0                  0.0             0.0   
3      Bockenheim                 0.0                  0.0             0.0   
4         Bonames                 0.0                  0.0             0.0   

   Argentinian Restaurant  Art Museum  Arts & Crafts Store  Asian Restaurant  \
0                     0.0    0.044944             0.000000           0.00000   
1                     0.0    0.000000             0.000000           0.00000   
2                     0.0    0.000000             0.000000           0.00000   
3                     0.0    0.000000             0.016393           0.04918   
4                     0.0    0.000000             0.000000           0.00000   

   Athletics & Sports  Austrian Restaurant  Auto Garage  Automotive Shop  \
0            0.000000             0.011236          0.0              0.0   
1            0.000000             0.000000          0.0              0.0   
2            0.000000             0.000000          0.0              0.0   
3            0.016393             0.000000          0.0              0.0   
4            0.000000             0.000000          0.0              0.0   

     Bakery      Bank       Bar  Beer Bar  Beer Garden    Bistro  Board Shop  \
0  0.011236  0.000000  0.022472  0.011236          0.0  0.022472    0.011236   
1  0.000000  0.000000  0.000000  0.000000          0.0  0.000000    0.000000   
2  0.000000  0.000000  0.000000  0.000000          0.0  0.000000    0.000000   
3  0.016393  0.016393  0.000000  0.000000          0.0  0.000000    0.000000   
4  0.111111  0.000000  0.000000  0.000000          0.0  0.000000    0.000000   

   Boarding House  Bookstore  Boutique  Breakfast Spot  Brewery  Building  \
0             0.0        0.0  0.022472        0.011236      0.0       0.0   
1             0.0        0.0  0.000000        0.000000      0.0       0.0   
2             0.0        0.0  0.000000        0.000000      0.0       0.0   
3             0.0        0.0  0.000000        0.000000      0.0       0.0   
4             0.0        0.0  0.000000        0.000000      0.0       0.0   

   Burger Joint  Bus Stop  Business Service   Butcher  Cafeteria      Café  \
0      0.044944  0.011236               0.0  0.000000        0.0  0.101124   
1      0.000000  0.000000               0.0  0.000000        0.0  0.000000   
2      0.000000  0.000000               0.0  0.000000        0.0  0.000000   
3      0.016393  0.000000               0.0  0.016393        0.0  0.098361   
4      0.000000  0.000000               0.0  0.000000        0.0  0.222222   

   Cajun / Creole Restaurant  Castle  Chinese Restaurant  Chocolate Shop  \
0                        0.0     0.0            0.011236        0.011236   
1                        0.0     0.0            0.000000        0.000000   
2                        0.0     0.0            0.000000        0.000000   
3                        0.0     0.0            0.016393        0.000000   
4                        0.0     0.0            0.000000        0.000000   

     Church  Cigkofte Place  Climbing Gym  Clothing Store  Cocktail Bar  \
0  0.011236             0.0           0.0        0.011236      0.011236   
1  0.000000             0.0           0.0        0.000000      0.000000   
2  0.000000             0.0           0.0        0.000000      0.000000   
3  0.000000             0.0           0.0        0.000000      0.016393   
4  0.000000             0.0           0.0        0.000000      0.000000   

   Coffee Shop  College Residence Hall  Comedy Club  Concert Hall  \
0     0.033708                     0.0          0.0           0.0   
1     0.000000                     0.0          0.0           0.0   
2     0.000000                     0.0          0.0           0.0   
3    

In [36]:
#create dataframe with most common venues per district
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [37]:
num_top_venues = 10

indicators = ['st', 'nd','rd']

columns = ['District']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

districts_sorted_venues = pd.DataFrame(columns=columns)
districts_sorted_venues['District'] = frankfurt_grouped['District']

for ind in np.arange(frankfurt_grouped.shape[0]):
    districts_sorted_venues.iloc[ind, 1:] = return_most_common_venues(frankfurt_grouped.iloc[ind, :], num_top_venues)

In [40]:
districts_sorted_venues.head()

District 1st Most Common Venue 2nd Most Common Venue  \
0        Altstadt                  Café                 Plaza   
1  Bergen-Enkheim                 Plaza              Fountain   
2     Berkersheim           Supermarket     German Restaurant   
3      Bockenheim                  Café    Italian Restaurant   
4         Bonames         Metro Station                  Café   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0            Restaurant            Art Museum          Burger Joint   
1            Food Court     Food & Drink Shop                  Food   
2                 Trail    Light Rail Station                   Zoo   
3      Asian Restaurant           Supermarket   Japanese Restaurant   
4    Italian Restaurant     German Restaurant      Doner Restaurant   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0     German Restaurant           Coffee Shop        Scenic Lookout   
1        Farmers Market    Falafel Restaurant               Exhibit   
2  Ethiopian Restaurant            Food Court     Food & Drink Shop   
3              Wine Bar        Ice Cream Shop    Spanish Restaurant   
4                Bakery        Ice Cream Shop        Discount Store   

  9th Most Common Venue 10th Most Common Venue  
0    Italian Restaurant                    Bar  
1           Event Space   Ethiopian Restaurant  
2                  Food         Farmers Market  
3    Turkish Restaurant              Drugstore  
4    Falafel Restaurant             Food Truck

In [41]:
# Cluster the districts into 5 clusters
kcluster = 5

frankfurt_grouped_clustering = frankfurt_grouped.drop('District', 1)

#run k means clustering
kmeans = KMeans(n_clusters = kcluster, random_state=0).fit(frankfurt_grouped_clustering)


In [45]:
#Summarize results in a dataframe
districts_sorted_venues.insert(0, 'Cluster Labels', kmeans.labels_)

frankfurt_merged = location_data

frankfurt_merged = frankfurt_merged.join(districts_sorted_venues.set_index('District'), on='District')

In [48]:
frankfurt_merged.head()

District   Latitude  Longitude  Cluster Labels  \
0                  Altstadt  50.110442   8.682901               0   
1                Innenstadt  50.112993   8.674341               0   
2  Gutleut-/Bahnhofsviertel  50.105651   8.668154               0   
3               Westend-Süd  50.115245   8.662270               0   
4              Westend-Nord  50.126356   8.667921               0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0                  Café                 Plaza            Restaurant   
1           Coffee Shop                 Hotel                 Plaza   
2                 Hotel                   Bar     Indian Restaurant   
3    Italian Restaurant            Steakhouse                Bakery   
4                  Café           Coffee Shop     French Restaurant   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0            Art Museum          Burger Joint     German Restaurant   
1              Boutique                  Café            Steakhouse   
2            Restaurant      Asian Restaurant    Seafood Restaurant   
3  Gym / Fitness Center     French Restaurant    Chinese Restaurant   
4       Thai Restaurant             Cafeteria    Spanish Restaurant   

  7th Most Common Venue  8th Most Common Venue 9th Most Common Venue  \
0           Coffee Shop         Scenic Lookout    Italian Restaurant   
1  Gym / Fitness Center      Electronics Store   Japanese Restaurant   
2           Coffee Shop  Vietnamese Restaurant                  Park   
3            Restaurant       Ramen Restaurant           Supermarket   
4                Garden                 Bistro  Ethiopian Restaurant   

       10th Most Common Venue  
0                         Bar  
1                  Restaurant  
2  Modern European Restaurant  
3                      Bistro  
4                 Supermarket

In [51]:
#Visualize the clusters
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kcluster)
ys = [i + x + (i*x)**2 for i in range(kcluster)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(frankfurt_merged['Latitude'], frankfurt_merged['Longitude'], frankfurt_merged['District'], frankfurt_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [56]:
frankfurt_merged.loc[frankfurt_merged['Cluster Labels'] == 0, frankfurt_merged.columns[[0] + list(range(4, frankfurt_merged.shape[1]))]]

District 1st Most Common Venue 2nd Most Common Venue  \
0                   Altstadt                  Café                 Plaza   
1                 Innenstadt           Coffee Shop                 Hotel   
2   Gutleut-/Bahnhofsviertel                 Hotel                   Bar   
3                Westend-Süd    Italian Restaurant            Steakhouse   
4               Westend-Nord                  Café           Coffee Shop   
5               Nordend-West    Italian Restaurant                  Café   
6                Nordend-Ost                  Café    Italian Restaurant   
7                     Ostend               Exhibit                 Hotel   
8                   Bornheim     German Restaurant                  Café   
9             Gutleutviertel                 Hotel    Italian Restaurant   
10                    Gallus      Asian Restaurant     German Restaurant   
11                Bockenheim                  Café    Italian Restaurant   
12        Sachsenhausen-Nord          Tram Station                   Spa   
15                 Niederrad                Bakery      Asian Restaurant   
17                 Griesheim                 River              Pie Shop   
18                 Rödelheim       Thai Restaurant     Indian Restaurant   
19                    Hausen         Metro Station              Bus Stop   
23                  Ginnheim           Supermarket                Bakery   
24                 Dornbusch           Pizza Place                  Park   
27              Preungesheim         Metro Station           Supermarket   
28                   Bonames         Metro Station                  Café   
30                Riederwald    Italian Restaurant     Convenience Store   
33                    Höchst                 Hotel             Drugstore   
35                Sindlingen           IT Services       Thai Restaurant   
37           Unterliederbach              Platform                 Hotel   
40          Kalbach-Riedberg           IT Services     Indian Restaurant   
41                   Harheim                Bakery                 Hotel   
42           Nieder-Eschbach                 Hotel     German Restaurant   

   3rd Most Common Venue 4th Most Common Venue     5th Most Common Venue  \
0             Restaurant            Art Museum              Burger Joint   
1                  Plaza              Boutique                      Café   
2      Indian Restaurant            Restaurant          Asian Restaurant   
3                 Bakery  Gym / Fitness Center         French Restaurant   
4      French Restaurant       Thai Restaurant                 Cafeteria   
5        Thai Restaurant      Theme Restaurant                   Brewery   
6                 Bakery                   Pub               Pizza Place   
7                   Café     German Restaurant               Supermarket   
8     Spanish Restaurant    Italian Restaurant              Cocktail Bar   
9             Restaurant                Bistro        African Restaurant   
10                   Bar          Concert Hall       Japanese Restaurant   
11      Asian Restaurant           Supermarket       Japanese Restaurant   
12      Greek Restaurant           Supermarket         German Restaurant   
15             Drugstore          Tram Station          Sushi Restaurant   
17           Yoga Studio           Supermarket         Electronics Store   
18           Supermarket    Chinese Restaurant                      Bank   
19                Bakery     German Restaurant             Grocery Store   
23                 Plaza      Asian Restaurant         Trattoria/Osteria   
24         Metro Station              Pharmacy  Mediterranean Restaurant   
27          Liquor Store          Climbing Gym      Gym / Fitness Center   
28    Italian Restaurant     German Restaurant          Doner Restaurant   
30           Supermarket         Metro Station                Hobby Shop   
33                  Café           Supermarket         German Resta

In [57]:
frankfurt_merged.loc[frankfurt_merged['Cluster Labels'] == 1, frankfurt_merged.columns[[0] + list(range(4, frankfurt_merged.shape[1]))]]

District 1st Most Common Venue 2nd Most Common Venue  \
21  Heddernheim     German Restaurant           Pizza Place   
22  Niederursel     German Restaurant           Pizza Place   
29  Berkersheim           Supermarket     German Restaurant   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
21           Supermarket    Falafel Restaurant                Bakery   
22           Supermarket                 Trail             Drugstore   
29                 Trail    Light Rail Station                   Zoo   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
21         Metro Station      Department Store            Food Court   
22     Food & Drink Shop                  Food        Farmers Market   
29  Ethiopian Restaurant            Food Court     Food & Drink Shop   

   9th Most Common Venue 10th Most Common Venue  
21     Food & Drink Shop                   Food  
22    Falafel Restaurant                Exhibit  
29                  Food         Farmers Market

In [58]:
frankfurt_merged.loc[frankfurt_merged['Cluster Labels'] == 2, frankfurt_merged.columns[[0] + list(range(4, frankfurt_merged.shape[1]))]]

District 1st Most Common Venue 2nd Most Common Venue  \
43  Bergen-Enkheim                 Plaza              Fountain   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
43            Food Court     Food & Drink Shop                  Food   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
43        Farmers Market    Falafel Restaurant               Exhibit   

   9th Most Common Venue 10th Most Common Venue  
43           Event Space   Ethiopian Restaurant

In [59]:
frankfurt_merged.loc[frankfurt_merged['Cluster Labels'] == 3, frankfurt_merged.columns[[0] + list(range(4, frankfurt_merged.shape[1]))]]

District 1st Most Common Venue 2nd Most Common Venue  \
13  Sachsenhausen-Süd                  Food     German Restaurant   
14            Oberrad          Tram Station     German Restaurant   
31           Seckbach                 Plaza    Photography Studio   
34               Nied          Tram Station           Pizza Place   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
13          Tram Station                  Lake                   Zoo   
14          Liquor Store                 Plaza        Ice Cream Shop   
31     German Restaurant               Dog Run     Electronics Store   
34    Light Rail Station           Supermarket     German Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
13     Electronics Store            Food Court     Food & Drink Shop   
14    Italian Restaurant       Laundry Service                   Zoo   
31     Food & Drink Shop                  Food        Farmers Market   
34                   Bar     Food & Drink Shop                  Food   

   9th Most Common Venue 10th Most Common Venue  
13        Farmers Market     Falafel Restaurant  
14                  Food         Farmers Market  
31    Falafel Restaurant                Exhibit  
34        Farmers Market     Falafel Restaurant

In [60]:
frankfurt_merged.loc[frankfurt_merged['Cluster Labels'] == 4, frankfurt_merged.columns[[0] + list(range(4, frankfurt_merged.shape[1]))]]

District 1st Most Common Venue 2nd Most Common Venue  \
16        Schwanheim     German Restaurant             Drugstore   
20         Praunheim           Supermarket     German Restaurant   
25       Eschersheim         Grocery Store              Bus Stop   
26         Eckenheim          Soccer Field              Bus Stop   
32        Fechenheim           Pizza Place           Supermarket   
36         Zeilsheim          Home Service    Italian Restaurant   
38        Sossenheim                Bakery        Ice Cream Shop   
39  Nieder-Erlenbach     Food & Drink Shop      Business Service   
44  Frankfurter Berg           Supermarket           Pizza Place   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
16            Restaurant        Ice Cream Shop                Museum   
20    Italian Restaurant             Racetrack        Discount Store   
25            Restaurant    Light Rail Station           Supermarket   
26                Market           Supermarket        Farmers Market   
32          Tram Station           Auto Garage     Electronics Store   
36           Supermarket     German Restaurant                   Zoo   
38        Shipping Store           Supermarket             Nightclub   
39           Supermarket     German Restaurant                   Zoo   
44    Light Rail Station              Bus Stop              Pharmacy   

        6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
16                Supermarket          Tram Station       Thai Restaurant   
20                        Gym            Restaurant                   Zoo   
25          Korean Restaurant     German Restaurant                 Plaza   
26  Cajun / Creole Restaurant           Beer Garden     German Restaurant   
32                 Food Court     Food & Drink Shop                  Food   
36          Electronics Store     Food & Drink Shop                  Food   
38          German Restaurant     Electronics Store                  Food   
39                   Fountain            Food Court                  Food   
44                       Food        Farmers Market    Falafel Restaurant   

   9th Most Common Venue 10th Most Common Venue  
16        Farmers Market     Falafel Restaurant  
20        Farmers Market     Falafel Restaurant  
25        Ice Cream Shop          Metro Station  
26            Food Truck             Food Court  
32        Farmers Market     Falafel Restaurant  
36        Farmers Market     Falafel Restaurant  
38        Farmers Market     Falafel Restaurant  
39        Farmers Market     Falafel Restaurant  
44               Exhibit            Event Space

## Interpretation

- We observe, that cluster "0" and "4" are the biggest clusters
- Cluster "4" seems to be slightly less central and the districts most common venues seem to be locations to acommodate households in their daily needs (eg bakeries, supermarkets, bus stops, etc.)
- Cluster "0" seems to be rather central and most common venues are often restaurants
- Therefore we should focus on cluster "0" for our own venue

- Cluster "0" also happens to have a lot of hotels, which indicates tourists and potential customers. Also due to the central position of the districts it is easily accessible for potential customers

### Now I will try to assess which of the districts in cluster 0 is the most beneficial for my new venue

##### First lets take a look at the overall population density:

In [61]:
map_ffm

In [111]:
frankfurt_merged['District']
visualize = frankfurt_merged['District'].loc[frankfurt_merged['Cluster Labels'] == 0]

In [123]:
vis_df = pd.DataFrame()
vis_df['District'] = visualize

In [124]:
vis_df

District
0                   Altstadt
1                 Innenstadt
2   Gutleut-/Bahnhofsviertel
3                Westend-Süd
4               Westend-Nord
5               Nordend-West
6                Nordend-Ost
7                     Ostend
8                   Bornheim
9             Gutleutviertel
10                    Gallus
11                Bockenheim
12        Sachsenhausen-Nord
15                 Niederrad
17                 Griesheim
18                 Rödelheim
19                    Hausen
23                  Ginnheim
24                 Dornbusch
27              Preungesheim
28                   Bonames
30                Riederwald
33                    Höchst
35                Sindlingen
37           Unterliederbach
40          Kalbach-Riedberg
41                   Harheim
42           Nieder-Eschbach

In [126]:
population = []
for item in vis_df['District']:
   population.append(ffm_pop.loc[ffm_pop['District']==item].values[0][1])

In [127]:
vis_df['Population'] = population

#### Now let's only look at the districts in cluster 0:

In [129]:
import folium

map_ffm_v2 = folium.Map(location=[50.110924, 8.682127], zoom_start=14)

In [130]:
map_ffm_v2.choropleth(geo_data=frankfurt_data,
    data=vis_df,
    columns=['District', 'Population'],
    key_on='feature.properties.STTLNAME',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Population Density Frankfurt'
)

/opt/conda/envs/Python-3.7-main/lib/python3.7/site-packages/folium/folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


In [132]:
folium.GeoJson(open('frankfurt_data.json', 'r', encoding='utf-8-sig').read(),
               name = 'District',
               tooltip=folium.GeoJsonTooltip(fields=('STTLNAME',),
               aliases=('District',)),
               show = True).add_to(map_ffm_v2)

In [133]:
map_ffm_v2

#### As we can see, the densest populated districts are:
- Bockenheim
- Gallus
- Sachsenhause-Nord
- Ostend
- Borhnheim
- Nordend-Ost
- Nordend-West

We can expect the highest number of resident customers in these areas

### Now we check for population density for our target age group of 18 to 64
- This age group has the most capital available for food and going out to a restaurant
- I want to compare if any district is dominant in this age group

In [248]:
visualize2 = frankfurt_merged['District'].loc[frankfurt_merged['Cluster Labels'] == 0]
vis_df2 = pd.DataFrame()
vis_df2['District'] = visualize2

In [292]:
population2 = []
for item in vis_df2['District']:
        population2.append(df_wmf.loc[df_wmf['District']==item].values[0][2])

In [294]:
vis_df2['Population'] = population2
vis_df2.head()

District  Population
0                  Altstadt        2628
1                Innenstadt        4845
2  Gutleut-/Bahnhofsviertel        7072
3               Westend-Süd       12038
4              Westend-Nord        6267

In [295]:
map_ffm_v3 = folium.Map(location=[50.110924, 8.682127], zoom_start=14)
map_ffm_v3.choropleth(geo_data=frankfurt_data,
    data=vis_df2,
    columns=['District', 'Population'],
    key_on='feature.properties.STTLNAME',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Population Density Frankfurt'
)

/opt/conda/envs/Python-3.7-main/lib/python3.7/site-packages/folium/folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


In [298]:
folium.GeoJson(open('frankfurt_data.json', 'r', encoding='utf-8-sig').read(),
               name = 'District',
               tooltip=folium.GeoJsonTooltip(fields=('STTLNAME',),
               aliases=('District',)),
               show = True).add_to(map_ffm_v3)

In [299]:
map_ffm_v3

### As we can see the districts are the same as when not checking for a specific age group, therefore the districts I will focus on are still the same

# Final Selection process
### Since I want to open a cafe I want to fulfill the following requirements:
- High population density in age group 18 to 64
- Close to public transportation and central of the city
- Area is populated with restaurants and hotels, so people will frequent the area a lot
- Cafes are not the most common venue, since competition will be too high

Until this point the following districts are still in the run:
- Bockenheim
- Gallus
- Sachsenhause-Nord
- Ostend
- Borhnheim
- Nordend-Ost
- Nordend-West

## First Eliminations
- Due to less optimal connection to public transport I will eliminate: Nordend-Ost/-West
- Due to less optimal age group density I will eliminate: Bornheim

In [301]:
frankfurt_merged.loc[frankfurt_merged['Cluster Labels'] == 0, frankfurt_merged.columns[[0] + list(range(4, frankfurt_merged.shape[1]))]]

District 1st Most Common Venue 2nd Most Common Venue  \
0                   Altstadt                  Café                 Plaza   
1                 Innenstadt           Coffee Shop                 Hotel   
2   Gutleut-/Bahnhofsviertel                 Hotel                   Bar   
3                Westend-Süd    Italian Restaurant            Steakhouse   
4               Westend-Nord                  Café           Coffee Shop   
5               Nordend-West    Italian Restaurant                  Café   
6                Nordend-Ost                  Café    Italian Restaurant   
7                     Ostend               Exhibit                 Hotel   
8                   Bornheim     German Restaurant                  Café   
9             Gutleutviertel                 Hotel    Italian Restaurant   
10                    Gallus      Asian Restaurant     German Restaurant   
11                Bockenheim                  Café    Italian Restaurant   
12        Sachsenhausen-Nord          Tram Station                   Spa   
15                 Niederrad                Bakery      Asian Restaurant   
17                 Griesheim                 River              Pie Shop   
18                 Rödelheim       Thai Restaurant     Indian Restaurant   
19                    Hausen         Metro Station              Bus Stop   
23                  Ginnheim           Supermarket                Bakery   
24                 Dornbusch           Pizza Place                  Park   
27              Preungesheim         Metro Station           Supermarket   
28                   Bonames         Metro Station                  Café   
30                Riederwald    Italian Restaurant     Convenience Store   
33                    Höchst                 Hotel             Drugstore   
35                Sindlingen           IT Services       Thai Restaurant   
37           Unterliederbach              Platform                 Hotel   
40          Kalbach-Riedberg           IT Services     Indian Restaurant   
41                   Harheim                Bakery                 Hotel   
42           Nieder-Eschbach                 Hotel     German Restaurant   

   3rd Most Common Venue 4th Most Common Venue     5th Most Common Venue  \
0             Restaurant            Art Museum              Burger Joint   
1                  Plaza              Boutique                      Café   
2      Indian Restaurant            Restaurant          Asian Restaurant   
3                 Bakery  Gym / Fitness Center         French Restaurant   
4      French Restaurant       Thai Restaurant                 Cafeteria   
5        Thai Restaurant      Theme Restaurant                   Brewery   
6                 Bakery                   Pub               Pizza Place   
7                   Café     German Restaurant               Supermarket   
8     Spanish Restaurant    Italian Restaurant              Cocktail Bar   
9             Restaurant                Bistro        African Restaurant   
10                   Bar          Concert Hall       Japanese Restaurant   
11      Asian Restaurant           Supermarket       Japanese Restaurant   
12      Greek Restaurant           Supermarket         German Restaurant   
15             Drugstore          Tram Station          Sushi Restaurant   
17           Yoga Studio           Supermarket         Electronics Store   
18           Supermarket    Chinese Restaurant                      Bank   
19                Bakery     German Restaurant             Grocery Store   
23                 Plaza      Asian Restaurant         Trattoria/Osteria   
24         Metro Station              Pharmacy  Mediterranean Restaurant   
27          Liquor Store          Climbing Gym      Gym / Fitness Center   
28    Italian Restaurant     German Restaurant          Doner Restaurant   
30           Supermarket         Metro Station                Hobby Shop   
33                  Café           Supermarket         German Resta

## Bockenheim:
Bockenheim has the highest population (total and in target age group), but the most common venues are already cafes.
Therefore I will eliminate Bockenheim as well.

## Final Selection
Gallus, Sachsenhausen-Nord and Ostend are all pretty similar to each other and would all be suitable places to build my cafe.

Therefore I will give points from 1 to 10 for the following:
- Closeness to public transport (1 far and few, 10 many and close)
- Commonness of Cafes  (1 very common, 10 uncommon)
- Commonness of Hotels (1 uncommon, 10 very common)

### Gallus: 19 points
- Closeness to publich transport: 9 (the main station of frankfurt is in walking distance)
- Commonness of Cafes: 10 (not in the most common venue list)
- Commonness of Hotels: 0 (not in the most common venue list)

### Sachsenhausen-Nord: 16 points
- Closeness to publich transport: 9 (many tram stations and access to the eastern train station of frankfurt)
- Commonness of Cafes: 6 (7th most common venue)
- Commonness of Hotels: 1 (10th most common venue)

### Ostend: 15 points
- Closeness to publich transport: 4 (close to eastern train station of frankfurt)
- Commonness of Cafes: 3 (3rd most common venue)
- Commonness of Hotels: 8 (10th most common venue)


# Since Gallus achieves the most points and fulfills all other requisitions, I will open my cafe in the district "Gallus"